In [1]:
import pandas as pd
from datasets import Dataset, Audio
from tqdm import tqdm
import os
from pydub import AudioSegment
import torch
import torch
from transformers import WhisperForConditionalGeneration, WhisperProcessor, Seq2SeqTrainingArguments, Seq2SeqTrainer
from peft import LoraConfig, get_peft_model, prepare_model_for_kbit_training
from datasets import Dataset, Audio
import evaluate

c:\Users\omerf\anaconda3\envs\transformer\lib\site-packages\requests\__init__.py:86: RequestsDependencyWarning: Unable to find acceptable character detection dependency (chardet or charset_normalizer).
  warnings.warn(
c:\Users\omerf\anaconda3\envs\transformer\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
W0214 16:17:32.662000 16480 site-packages\torch\distributed\elastic\multiprocessing\redirects.py:29] NOTE: Redirects are currently not supported in Windows or MacOs.


In [2]:

print(torch.cuda.is_available())        # True olmalı
print(torch.version.cuda)               # 11.8 yazmalı
print(torch.cuda.get_device_name(0))    # GeForce RTX 3050ti


True
11.8
NVIDIA GeForce RTX 3050 Ti Laptop GPU


In [3]:
#mp3 den wav a dönüştürme scripti
def prepare_wav_files(csv_path, output_folder):
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)

    df = pd.read_csv(csv_path)
    print(f"Toplam {len(df)} dosya işleniyor...")

    for index, row in tqdm(df.iterrows(), total=df.shape[0]):
        mp3_path = row['filename']
        file_name = os.path.basename(mp3_path).replace(".mp3", ".wav")
        dest_path = os.path.join(output_folder, file_name)

        if not os.path.exists(dest_path):
            try:
                audio = AudioSegment.from_mp3(mp3_path)
                # Whisper standardı: 16kHz, Mono
                audio = audio.set_frame_rate(16000).set_channels(1)
                audio.export(dest_path, format="wav")
            except Exception as e:
                continue

    return output_folder

WAV_DIR = prepare_wav_files("cv-valid-train.csv", "cv-valid-train-wav")

Toplam 195776 dosya işleniyor...


100%|██████████| 195776/195776 [5:19:45<00:00, 10.20it/s]  


In [3]:
df = pd.read_csv("cv-valid-train.csv")
df['audio'] = df['filename'].apply(lambda x: os.path.join("cv-valid-train-wav", os.path.basename(x).replace(".mp3", ".wav")))
df = df.rename(columns={'text': 'sentence'})[['audio', 'sentence']]

df

audio  \
0       cv-valid-train-wav\sample-000000.wav   
1       cv-valid-train-wav\sample-000001.wav   
2       cv-valid-train-wav\sample-000002.wav   
3       cv-valid-train-wav\sample-000003.wav   
4       cv-valid-train-wav\sample-000004.wav   
...                                      ...   
195771  cv-valid-train-wav\sample-195771.wav   
195772  cv-valid-train-wav\sample-195772.wav   
195773  cv-valid-train-wav\sample-195773.wav   
195774  cv-valid-train-wav\sample-195774.wav   
195775  cv-valid-train-wav\sample-195775.wav   

                                                 sentence  
0       learn to recognize omens and follow them the o...  
1              everything in the universe evolved he said  
2       you came so that you could learn about your dr...  
3       so now i fear nothing because it was those ome...  
4       if you start your emails with greetings let me...  
...                                                   ...  
195771                        the englishman said nothing  
195772                       the irish man sipped his tea  
195773                        what do you know about that  
195774                 the phone rang while she was awake  
195775  among these people were a couple of cyclists a...  

[195776 rows x 2 columns]

In [4]:
dataset = Dataset.from_pandas(df)
dataset = dataset.cast_column("audio", Audio(sampling_rate=16000))

# Tüm veriyi işlemek yerine önce küçük bir kısmını seç
dataset = dataset.select(range(50000)) # Sadece ilk 20 bin dosyayı al
# Sonra yukarıdaki optimize edilmiş map işlemini yap

dataset

Dataset({
    features: ['audio', 'sentence'],
    num_rows: 50000
})

In [5]:
model_id = "openai/whisper-base"
processor = WhisperProcessor.from_pretrained(model_id)
model = WhisperForConditionalGeneration.from_pretrained(
    model_id,
    load_in_4bit=True,
    device_map="auto"
)


c:\Users\omerf\anaconda3\envs\transformer\lib\site-packages\huggingface_hub\file_download.py:943: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


In [6]:
model = prepare_model_for_kbit_training(model)
config = LoraConfig(
    r=32, lora_alpha=64, target_modules=["q_proj", "v_proj"],
    lora_dropout=0.05, bias="none"
)
model = get_peft_model(model, config)

In [7]:
model

PeftModel(
  (base_model): LoraModel(
    (model): WhisperForConditionalGeneration(
      (model): WhisperModel(
        (encoder): WhisperEncoder(
          (conv1): Conv1d(80, 512, kernel_size=(3,), stride=(1,), padding=(1,))
          (conv2): Conv1d(512, 512, kernel_size=(3,), stride=(2,), padding=(1,))
          (embed_positions): Embedding(1500, 512)
          (layers): ModuleList(
            (0-5): 6 x WhisperEncoderLayer(
              (self_attn): WhisperSdpaAttention(
                (k_proj): Linear4bit(in_features=512, out_features=512, bias=False)
                (v_proj): lora.Linear4bit(
                  (base_layer): Linear4bit(in_features=512, out_features=512, bias=True)
                  (lora_dropout): ModuleDict(
                    (default): Dropout(p=0.05, inplace=False)
                  )
                  (lora_A): ModuleDict(
                    (default): Linear(in_features=512, out_features=32, bias=False)
                  )
                  (lora_B): 

In [8]:
def prepare_dataset(batch):
    audio = batch["audio"]
    
    # Modelin beklediği giriş özelliklerini (input_features) hesapla
    batch["input_features"] = processor(
        audio["array"], 
        sampling_rate=audio["sampling_rate"]
    ).input_features[0]
    
    # Hedef metni (sentence) tokenize ederek etiketlere (labels) çevir
    batch["labels"] = processor.tokenizer(batch["sentence"]).input_ids
    return batch

In [10]:
print(f"Mevcut Sütunlar: {dataset['train'].column_names}")

Mevcut Sütunlar: ['input_features', 'labels']


In [9]:

dataset = dataset.map(
    prepare_dataset, 
    remove_columns=dataset.column_names,
    batched=False,             # Her seferinde tek dosya işle
    batch_size=1,              # RAM'de birikmeyi önle
    keep_in_memory=False,      # RAM yerine diski kullan (ÇOK KRİTİK!)
    load_from_cache_file=True, # Daha önce işlenenleri tekrar yapma
    num_proc=1                 # Çoklu işlem bazen RAM hatasını tetikler, 1 ile dene
)

# Önce böl
dataset = dataset.train_test_split(test_size=0.1)

dataset["train"] = dataset["train"].map(
    prepare_dataset, 
    # Sütunları silerken spesifik olarak train setinin sütunlarını hedefle
    remove_columns=dataset["train"].column_names, 
    keep_in_memory=False,
 ) # RAM yerine disk kullan

dataset["test"] = dataset["test"].map(
    prepare_dataset, 
    remove_columns=dataset["test"].column_names, 
    keep_in_memory=False,
    batched=False
)

Map:   0%|          | 0/45000 [00:00<?, ? examples/s]


KeyError: 'audio'

In [12]:
metric = evaluate.load("wer")

def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # Pad tokenlarını (özel karakterleri) temizle
    label_ids[label_ids == -100] = processor.tokenizer.pad_token_id

    pred_str = processor.tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = processor.tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    wer = 100 * metric.compute(predictions=pred_str, references=label_str)
    return {"wer": wer}

# Eğitim Parametreleri
training_args = Seq2SeqTrainingArguments(
    output_dir="./whisper-omer-project",
    per_device_train_batch_size=1, # VRAM dolmaması için 1
    gradient_accumulation_steps=16, # Efektif batch size = 16
    learning_rate=1e-3,
    max_steps=5000,
    gradient_checkpointing=True,
    fp16=True, # 3050 Ti'ın hızını kullanmak için
    evaluation_strategy="steps",
    save_steps=1000,
    logging_steps=25,
    eval_steps=100,
    predict_with_generate=True,
    remove_unused_columns=False,
    per_device_eval_batch_size=1,     # Değerlendirme sırasında tek tek işle
    eval_accumulation_steps=1,        # Bellekte sonuç biriktirme, hemen boşalt
    generation_max_length=128,        # Cümle uzunluğunu sınırla (VRAM tasarrufu)
    logging_first_step=True,
    
)

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=dataset["train"], # Sadece bu kalsın
    eval_dataset=dataset["test"],
    tokenizer=processor.feature_extractor,
    compute_metrics=compute_metrics,
)

# Eğitimi başlat
trainer.train()

c:\Users\omerf\anaconda3\envs\transformer\lib\site-packages\accelerate\accelerator.py:432: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(
c:\Users\omerf\anaconda3\envs\transformer\lib\site-packages\accelerate\accelerator.py:463: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)
wandb: ERROR Failed to detect the name of this notebook. You can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: omerfarukcirpan (omerfa

  0%|          | 0/5000 [00:00<?, ?it/s]c:\Users\omerf\anaconda3\envs\transformer\lib\site-packages\torch\_dynamo\eval_frame.py:838: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.5 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)
c:\Users\omerf\anaconda3\envs\transformer\lib\site-packages\torch\utils\checkpoint.py:86: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(
c:\Users\omerf\anaconda3\envs\transformer\lib\site-packages\bitsandbytes\nn\modules.py:463: UserWarning: Input type into Linear4bit is torch.float16, but bnb_4bit_compute_dtype=torch.float32 (default). This will lead to slow inference or training speed.
  warnings.warn(
c:\Users\

{'loss': 7.1076, 'grad_norm': 17.79623794555664, 'learning_rate': 0.0009998000000000001, 'epoch': 0.0}


{'loss': 0.9048, 'grad_norm': 1.119550347328186, 'learning_rate': 0.000995, 'epoch': 0.01}


{'loss': 0.2879, 'grad_norm': 0.5590431094169617, 'learning_rate': 0.00099, 'epoch': 0.02}


...

{'loss': 0.1867, 'grad_norm': 1.5498467683792114, 'learning_rate': 0.0006902000000000001, 'epoch': 0.55}


{'loss': 0.1802, 'grad_norm': 0.964836835861206, 'learning_rate': 0.0006852000000000001, 'epoch': 0.56}


{'loss': 0.1898, 'grad_norm': 0.7967449426651001, 'learning_rate': 0.0006802, 'epoch': 0.57}


 24%|██▎       | 1180/5000 [17:53<58:50,  1.08it/s]

KeyboardInterrupt: 

In [3]:
import torch
from transformers import WhisperForConditionalGeneration, WhisperProcessor
from peft import PeftModel
import librosa
import numpy as np

# 1. Ayarlar ve Dosya Yolları
model_id = "openai/whisper-base" 
checkpoint_path = "./whisper-omer-project/checkpoint-1000" 
test_audio_file = "mehmet_deneme.mp3" # Buraya kendi dosyanı yaz

print("Model ve İşlemci yükleniyor...")

# 2. Processor ve Model Yükleme (Öncekiyle aynı)
processor = WhisperProcessor.from_pretrained(
    model_id, 
    language="English", 
    task="transcribe",
    local_files_only=True
)

model = WhisperForConditionalGeneration.from_pretrained(
    model_id, 
    load_in_8bit=False, 
    device_map="auto",
    local_files_only=True
)

# LoRA Adapter entegrasyonu
model = PeftModel.from_pretrained(model, checkpoint_path)

print("Model hazır! Ses dosyası işleniyor...")

# 5. KUSURSUZ DÖNÜŞTÜRME KATMANI
# librosa.load fonksiyonuna sr=16000 eklediğimizde, dosya ne olursa olsun 
# otomatik olarak 16kHz'e resample edilir (yeniden örneklenir).
# mono=True ise sesi tek kanala indirger.
speech, sr = librosa.load(test_audio_file, sr=16000, mono=True)

# 5.1. Normalizasyon (Opsiyonel ama önerilir)
# Ses çok kısık veya çok yüksekse dengeler.
if np.abs(speech).max() > 0:
    speech = speech / np.abs(speech).max()

# 6. Özellik Çıkarımı ve Tahmin
input_features = processor(speech, sampling_rate=16000, return_tensors="pt").input_features.to("cuda")

with torch.no_grad():
    # max_length ekleyerek çok uzun dosyalarda kesilmesini önleyebilirsin
    predicted_ids = model.generate(input_features, max_length=255)

# 7. Sonuç
transcription = processor.batch_decode(predicted_ids, skip_special_tokens=True)[0]

print("\n" + "="*40)
print(f"MODEL ÇIKTISI: {transcription}")
print("="*40)

Model ve İşlemci yükleniyor...


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Model hazır! Ses dosyası işleniyor...

MODEL ÇIKTISI:  Can you hear me baby i'm coming for you you are a beautiful woman and i'll fuck you
